In [427]:
import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots

from typing import NamedTuple

from quantfreedom.enums import CandleBodyType
from quantfreedom.helper_funcs import dl_ex_candles
from quantfreedom.indicators.tv_indicators import macd_tv, ema_tv 


np.set_printoptions(formatter={"float_kind": "{:0.2f}".format})

%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [428]:
candles = dl_ex_candles(
    exchange="mufex",
    symbol='BTCUSDT',
    timeframe='30m',
    candles_to_dl=10000
    )

In [429]:
candles

array([[1695164400000.00, 27173.50, 27213.30, 27157.30, 27198.90, 3.95],
       [1695166200000.00, 27198.90, 27209.50, 27174.50, 27195.50, 3.16],
       [1695168000000.00, 27195.50, 27240.90, 27159.30, 27168.90, 6.42],
       ...,
       [1713159000000.00, 65083.40, 65492.70, 65048.80, 65435.00, 264.82],
       [1713160800000.00, 65435.00, 66353.40, 65317.90, 66308.00, 598.04],
       [1713162600000.00, 66308.00, 66522.60, 66051.60, 66430.80, 607.34]])

In [430]:
datetimes = candles[:, CandleBodyType.Timestamp].astype('datetime64[ms]')
closing_prices = candles[:, CandleBodyType.Close]
low_prices = candles[:, CandleBodyType.Low]

In [431]:
macd_below = 30
fast_length = 12
slow_length = 26
signal_smoothing = 9
ema_length = 200

In [432]:
histogram, macd, signal = macd_tv(
    source=closing_prices,
    fast_length=fast_length,
    slow_length=slow_length,
    signal_smoothing=signal_smoothing
    )

In [433]:
ema = ema_tv(
    source=closing_prices,
    length=ema_length
    )

In [434]:
prev_macd = np.roll(macd, 1)
prev_macd[0] = np.nan

prev_signal = np.roll(signal, 1)
prev_signal[0] = np.nan

In [435]:
macd_below_signal = prev_macd < prev_signal
macd_above_signal = macd > signal
low_price_below_ema = low_prices > ema
macd_below_number = macd < macd_below
macd_sell_signal = prev_macd > macd

In [436]:
entries = (
    (macd_above_signal == True)
    & (macd_below_number == True)
    )
entries

array([False, False, False, ..., False, False, False])

In [437]:
entry_signals = np.where(entries, macd, np.nan)
entry_signals

array([nan, nan, nan, ..., nan, nan, nan])

In [438]:
exits = (
    (macd_below_signal == False)
    & (macd_above_signal == True)
    & (macd_below_number == False)
    & (macd_sell_signal == True)
    )
exits

array([False, False, False, ..., False, False, False])

In [439]:
exit_signals = np.where(exits, macd, np.nan)
exit_signals

array([nan, nan, nan, ..., nan, nan, nan])

In [440]:
fig = go.Figure()
fig = make_subplots(
    cols=1,
    rows=2,
    shared_xaxes=True,
    subplot_titles=("Candles", "MACD"),
    row_heights=[0.6, 0.4],
    vertical_spacing=0.1
    )
# Candlestick chart
fig.append_trace(
    go.Candlestick(
        x=datetimes,
        open=candles[:, CandleBodyType.Open],
        high=candles[:, CandleBodyType.High],
        low=candles[:, CandleBodyType.Low],
        close=candles[:, CandleBodyType.Close],
        name="Candles"
        ),
    row=1,
    col=1
)
fig.append_trace(
    go.Scatter(
        x=datetimes,
        y=ema,
        mode='lines',
        name='EMA',
        line_color='yellow',
    ),
    row=1,
    col=1
)
ind_shift = np.roll(histogram, 1)
ind_shift[0] = np.nan
colors = np.where(
    histogram >= 0,
    np.where(ind_shift < histogram, '#26A69A', '#B2DFDB'),
    np.where(ind_shift < histogram, '#FFCDD2', '#FF5252'),
)
fig.append_trace(
    go.Bar(
        x=datetimes,
        y=histogram,
        name='Histogram',
        marker_color=colors,
    ),
    row=2,
    col=1
)
fig.append_trace(
    go.Scatter(
        x=datetimes,
        y=macd,
        name='macd',
        line_color='#2962FF',
    ),
    row=2,
    col=1,
)
fig.append_trace(
    go.Scatter(
        x=datetimes,
        y=signal,
        name='signal',
        line_color='#FF6D00',
    ),
    row=2,
    col=1,
)
fig.append_trace(
    go.Scatter(
        x=datetimes,
        y=entry_signals,
        mode='markers',
        name='entries',
        marker=dict(
            size=12,
            symbol='circle',
            color='#00F6FF',
            line=dict(
                width=1,
                color='DarkSlateGrey'
            )
        ),
    ),
    row=2,
    col=1,
)
fig.append_trace(
    go.Scatter(
        x=datetimes,
        y=exit_signals,
        mode='markers',
        name='exits',
        marker=dict(
            size=12,
            symbol='star',
            color='green',
            line=dict(
                width=1,
                color='DarkSlateGrey'
            )
        ),
    ),
    row=2,
    col=1,
)
# Update options and show the plot
fig.update_layout(height=800, xaxis_rangeslider_visible=False)
fig.show()